In [2]:
import kmapper as km
import matplotlib.pyplot as plt
import numpy as np
import sklearn
import tadasets
import pandas as pd

In [3]:
import pandas as pd
import kmapper as km
import sklearn
import numpy as np
from IPython.display import display, HTML
import yfinance 
from sklearn.manifold import Isomap
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
import matplotlib.pyplot as plt
#from umap.umap_ import UMAP

In [4]:
df = pd.read_csv('COVID19.csv')

In [5]:
# Contar los casos confirmados por día
casos_por_dia = df.groupby('FECHA_SINTOMAS')['CLASIFICACION_FINAL'].count().reset_index(name='NUM_CASOS_CONFIRMADOS')

# Merge para añadir la columna de casos confirmados al DataFrame original
df_final = pd.merge(df, casos_por_dia, on='FECHA_SINTOMAS', how='left')

In [6]:
df_final

FECHA_ACTUALIZACION FECHA_SINTOMAS          ENTIDAD_NAC  latitud_nac  \
0               2024-04-16     2023-01-30               Colima    19.242922   
1               2024-04-16     2023-02-14  Baja California Sur    25.938501   
2               2024-04-16     2023-01-08              Jalisco    20.580795   
3               2024-04-16     2023-01-02             Guerrero    17.668085   
4               2024-04-16     2023-05-08               Colima    19.242922   
...                    ...            ...                  ...          ...   
433185          2024-04-16     2023-08-27               Colima    19.242922   
433186          2024-04-16     2023-08-28               Colima    19.242922   
433187          2024-04-16     2023-08-28              Jalisco    20.580795   
433188          2024-04-16     2023-08-29               Colima    19.242922   
433189          2024-04-16     2023-08-29               Colima    19.242922   

        longitud_nac          ENTIDAD_RES  latitud_res  longitud_res  \
0        -103.728119               Colima    19.242922   -103.728119   
1        -112.061226  Baja California Sur    25.938501   -112.061226   
2        -103.613129               Colima    19.242922   -103.728119   
3         -99.921646               Colima    19.242922   -103.728119   
4        -103.728119               Colima    19.242922   -103.728119   
...              ...                  ...          ...           ...   
433185   -103.728119              Jalisco    20.580795   -103.613129   
433186   -103.728119              Jalisco    20.580795   -103.613129   
433187   -103.613129              Jalisco    20.580795   -103.613129   
433188   -103.728119               Colima    19.242922   -103.728119   
433189   -103.728119              Jalisco    20.580795   -103.613129   

        CLASIFICACION_FINAL  NUM_CASOS_CONFIRMADOS  
0                         3                   3733  
1                         3                   3087  
2                         3                   4533  
3                         3                   6367  
4                         3                   1285  
...                     ...                    ...  
433185                    3                   1321  
433186                    3                   1736  
433187                    3                   1736  
433188                    3                   1445  
433189                    3                   1445  

[433190 rows x 10 columns]

In [7]:
import pandas as pd

# Supongamos que df es tu DataFrame y 'FECHA_SINTOMAS' es tu columna de fecha en formato string
# Primero, convertir la columna de fecha de string a datetime
df_final['FECHA_SINTOMAS'] = pd.to_datetime(df_final['FECHA_SINTOMAS'], format='%Y-%m-%d')

# Ahora, convertir la fecha a un número ordinal (número de días desde una fecha mínima común)
df_final['FECHA_SINTOMAS_ORDINAL'] = (df_final['FECHA_SINTOMAS'] - df_final['FECHA_SINTOMAS'].min()).dt.days

# O convertir la fecha a Unix timestamp (segundos desde 1970-01-01)
df_final['FECHA_SINTOMAS_UNIX'] = (df_final['FECHA_SINTOMAS'] - pd.Timestamp("1970-01-01")) // pd.Timedelta('1s')

# Luego puedes normalizar esta columna si es necesario para tu algoritmo de aprendizaje automático


### Normalización


In [8]:
# Seleccionar las características relevantes
features = ['FECHA_SINTOMAS_ORDINAL','NUM_CASOS_CONFIRMADOS', 'latitud_res', 'longitud_res']

# Normalizar las características
#df_normalized = scaler.fit_transform(df_final[features])

In [9]:
data = df_final[['FECHA_SINTOMAS_ORDINAL','NUM_CASOS_CONFIRMADOS','latitud_res', 'longitud_res']].to_numpy()

In [10]:
scaler = StandardScaler()
df_normalized = scaler.fit_transform(data)

### Mapper

In [30]:
mapper = km.KeplerMapper(verbose=1)
# La proyección sobre el math score, corresponde a proyectar sobre la primera columna de data
projected_data = mapper.fit_transform(df_normalized, projection=[0,1], scaler=None) 

covering=km.Cover(n_cubes=10,perc_overlap=0.08)

import warnings

# Ignorar todas las advertencias
warnings.filterwarnings('ignore')

G = mapper.map(projected_data, data, clusterer=sklearn.cluster.KMeans(n_clusters=3),cover=covering)

mapper.visualize(G, 
                path_html="mapper_visualization_output.html",
                 title="Mapper on COVID19 Data",
                #custom_tooltips = performance_data['gender'].to_numpy(),
                #color_values = mean,
                #color_function_name = 'Mean of Reading and Writing Score',
                node_color_function=np.array(['average','std','sum','max','min']))

#display(HTML('performance_math_score.html'))

KeplerMapper(verbose=1)
..Composing projection pipeline of length 1:
	Projections: [0, 1]
	Distance matrices: False
	Scalers: None
..Projecting on data shaped (433190, 4)

..Projecting data using: [0, 1]
Mapping on data shaped (433190, 4) using lens shaped (433190, 2)

Creating 100 hypercubes.

Created 50 edges and 93 nodes in 0:00:04.796613.
Wrote visualization to: mapper_visualization_output.html


'<!DOCTYPE html>\n<html>\n\n<head>\n  <meta charset="utf-8">\n  <meta name="generator" content="KeplerMapper">\n  <title>Mapper on COVID19 Data | KeplerMapper</title>\n\n  <link rel="icon" type="image/png" href="http://i.imgur.com/axOG6GJ.jpg" />\n\n  <link href=\'https://fonts.googleapis.com/css?family=Roboto+Mono:700,300\' rel=\'stylesheet\' type=\'text/css\'>\n  <style>* {\n  margin: 0;\n  padding: 0;\n}\n\nhtml, body {\n  height: 100%;\n}\n\nbody {\n  font-family: "Roboto Mono", "Helvetica", sans-serif;\n  font-size: 14px;\n}\n\n#logo {\n  width:  85px;\n  height: 85px;\n}\n\n#display {\n  color: #95A5A6;\n  background: #212121;\n}\n\n#header {\n  background: #111111;\n}\n\n#print {\n  color: #000;\n  background: #FFF;\n}\n\nh1 {\n  font-size: 21px;\n  font-weight: 300;\n  font-weight: 300;\n}\n\nh2 {\n  font-size: 18px;\n  padding-bottom: 20px;\n  font-weight: 300;\n}\n\nh3 {\n  font-size: 14px;\n  font-weight: 700;\n  text-transform: uppercase;\n}\n\nh4 {\n  font-size: 13px;\n  f

In [32]:
G['meta_data']

{'projection': '[0, 1]',
 'n_cubes': 10,
 'perc_overlap': 0.08,
 'clusterer': 'KMeans(n_clusters=3)',
 'scaler': 'None'}

In [33]:
cluster_cube16_cluster1 = G['nodes']['cube16_cluster1']

In [34]:
len(G['nodes'])

93

In [38]:
# Supongamos que 'graph' es tu grafo mapper ya creado.
# 'df' es tu DataFrame original.

# Acceder a los nodos en el grafo
for node_id, indices in G['nodes'].items():
    print(f"Node {node_id} contiene los siguientes índices de puntos de datos: {indices}")
    
    # Acceder a los puntos de datos correspondientes en el DataFrame
    data_points = df.loc[indices]
    
    # Ahora puedes hacer algo con esos puntos de datos
data_points


Node cube0_cluster0 contiene los siguientes índices de puntos de datos: [113399, 113623, 113921, 114203, 114234, 114806, 115134, 115142, 115163, 115252, 115261, 115289, 115290, 115312, 115313, 115353, 115416, 115435, 115450, 115474, 115495, 115512, 115523, 115651, 115653, 115681, 115684, 115685, 115692, 115719, 115745, 115748, 115763, 115768, 115780, 116002, 116007, 116008, 116012, 116013, 116019, 116020, 116024, 116025, 116029, 116032, 116033, 116035, 116038, 116042, 116044, 116126, 116193, 116280, 116506, 116528, 116685, 116782, 116793, 116813, 116908, 116973, 117077, 117164, 117646, 117722, 117748, 117767, 117836, 117865, 117872, 118084, 118149, 118189, 118303, 118325, 118369, 118434, 118497, 118522, 118630, 118751, 118810, 118816, 118856, 119031, 119290, 119326, 119373, 119388, 119472, 119700, 119861, 120011, 120063, 120172, 120189, 120285, 120309, 120422, 120429, 120633, 120679, 120988, 121038, 121206, 121394, 121835, 122150, 122240, 122642, 123163, 123394, 123454, 123562, 123573,

FECHA_ACTUALIZACION FECHA_SINTOMAS ENTIDAD_NAC  latitud_nac  \
430624          2024-04-16     2024-02-29   Querétaro    20.855104   
430647          2024-04-16     2024-02-29      Colima    19.242922   
430697          2024-04-16     2024-02-29   Querétaro    20.855104   
430698          2024-04-16     2024-02-29   Querétaro    20.855104   
430711          2024-04-16     2024-02-29     Jalisco    20.580795   
...                    ...            ...         ...          ...   
431907          2024-04-16     2024-03-10      Puebla    19.033001   
431936          2024-04-16     2024-03-20     Jalisco    20.580795   
432008          2024-04-16     2024-03-11      Puebla    19.033001   
432009          2024-04-16     2024-03-04      Puebla    19.033001   
432192          2024-04-16     2024-03-04  Nuevo León    25.572596   

        longitud_nac ENTIDAD_RES  latitud_res  longitud_res  \
430624    -99.845810   Querétaro    20.855104    -99.845810   
430647   -103.728119      Colima    19.242922   -103.728119   
430697    -99.845810   Querétaro    20.855104    -99.845810   
430698    -99.845810   Querétaro    20.855104    -99.845810   
430711   -103.613129     Jalisco    20.580795   -103.613129   
...              ...         ...          ...           ...   
431907    -98.182999      Puebla    19.033001    -98.182999   
431936   -103.613129     Jalisco    20.580795   -103.613129   
432008    -98.182999      Puebla    19.033001    -98.182999   
432009    -98.182999      Puebla    19.033001    -98.182999   
432192    -99.968971  Nuevo León    25.572596    -99.968971   

        CLASIFICACION_FINAL  
430624                    3  
430647                    3  
430697                    3  
430698                    3  
430711                    3  
...                     ...  
431907                    3  
431936                    3  
432008                    3  
432009                    3  
432192                    3  

[574 rows x 9 columns]